In [1]:
from torchkf import *
import torch
import numpy as np


import plotly.graph_objs as go
import plotly.express as px
import pykeos as pk

pyunicorn: Package netCDF4 could not be loaded. Some functionality in class Data might not be available!
pyunicorn: Package netCDF4 could not be loaded. Some functionality in class NetCDFDictionary might not be available!


In [16]:
pE = np.array([18., 18., 46.92, 2., 1., 2., 4., 1., 1., 1.])

def lorenz(x, v, P):
    x0 = P[0] * x[1] - P[1] * x[0]
    x1 = P[2] * x[0] - P[3] * x[2] * x[0] - P[4] * x[1]
    x2 = P[5] * x[0] * x[1] - P[6] * x[2]
    
    return np.array([x0, x1, x2])

def obs(x, v, P): 
    return np.array(x.T @ P[-3:])

models = [GaussianModel(
    f=lorenz, 
    g=obs, 
    x=np.array([0.9,0.8,30])[:, None], pE=pE, sv=1/8., sw=1/8., m=1, 
    n=3, W=np.array([[np.exp(-8)] * 3]), V=np.array([[np.exp(0)]]), 
)]

nT = 1024
hdm = HierarchicalGaussianModel(*models, dt=1/128.)
gen = DEMInversion(hdm, states_embedding_order=3).generate(nT)
y   = gen.v[:, 0, :1, 0]

Compiling derivatives, it might take some time... 
  Compiling f... f() ok. (compiled in 0.01s)
  Compiling g... g() ok. (compiled in 0.00s)
Done. 


  0%|          | 0/1024 [00:00<?, ?it/s]

In [3]:
def generalized_coordinates(
        x    : np.ndarray,    # timeseries
        p    : int,             # embedding order,
        dt   : int = 1          # sampling interval
        ):
        """ series: torch tensor (n_times, dim) 
            inspired from spm_DEM_embed.m by Karl Friston
            series_generalized = T * [series[t-order/2], dots, series[t+order/2]]
        """
        n_times, dim = x.shape
        
        # Make sure the input is a numpy array 
        x     = np.array(x, dtype='d')
        
        # Time and embedding order
        times = np.arange(1, n_times + 1)
        ks    = np.arange(1, p + 1)
        
        # Taylor's expansion forward (T) and inverse (E) operators
        T = np.empty((p, p), dtype='d')
        E = np.empty((p, p), dtype='d')
        
        # Embedded time series (for output)
        X = np.zeros((n_times, p, dim))
        
        for t in times:
            s = float(t)
            k = ks + int(np.fix(s - (p + 1) / 2.))
            y = s - min(k) + 1
            k = np.clip(k, 1, n_times)
            print(s, k, y, k)

            # Create T_ij(t) (note that indices start at 0) 
            for i in range(p): 
                for j in range(p): 
                    T[i, j] = float( ((i - y + 1) * dt)**j / np.math.factorial(j))
            
            # Compute E
            E[:] = np.linalg.inv(T)
            
            # Embed
            X[t - 1] = E @ x[k - 1]

        return X

In [4]:
generalized_coordinates(np.)

SyntaxError: invalid syntax (<ipython-input-4-130b4904f746>, line 1)

In [17]:
px.line(y=generalized_coordinates(z[0], 3, 1/128.)[:, 0, 0])

1.0 [1 1 2] 2.0 [1 1 2]
2.0 [1 2 3] 2.0 [1 2 3]
3.0 [2 3 4] 2.0 [2 3 4]
4.0 [3 4 5] 2.0 [3 4 5]
5.0 [4 5 6] 2.0 [4 5 6]
6.0 [5 6 7] 2.0 [5 6 7]
7.0 [6 7 8] 2.0 [6 7 8]
8.0 [7 8 9] 2.0 [7 8 9]
9.0 [ 8  9 10] 2.0 [ 8  9 10]
10.0 [ 9 10 11] 2.0 [ 9 10 11]
11.0 [10 11 12] 2.0 [10 11 12]
12.0 [11 12 13] 2.0 [11 12 13]
13.0 [12 13 14] 2.0 [12 13 14]
14.0 [13 14 15] 2.0 [13 14 15]
15.0 [14 15 16] 2.0 [14 15 16]
16.0 [15 16 17] 2.0 [15 16 17]
17.0 [16 17 18] 2.0 [16 17 18]
18.0 [17 18 19] 2.0 [17 18 19]
19.0 [18 19 20] 2.0 [18 19 20]
20.0 [19 20 21] 2.0 [19 20 21]
21.0 [20 21 22] 2.0 [20 21 22]
22.0 [21 22 23] 2.0 [21 22 23]
23.0 [22 23 24] 2.0 [22 23 24]
24.0 [23 24 25] 2.0 [23 24 25]
25.0 [24 25 26] 2.0 [24 25 26]
26.0 [25 26 27] 2.0 [25 26 27]
27.0 [26 27 28] 2.0 [26 27 28]
28.0 [27 28 29] 2.0 [27 28 29]
29.0 [28 29 30] 2.0 [28 29 30]
30.0 [29 30 31] 2.0 [29 30 31]
31.0 [30 31 32] 2.0 [30 31 32]
32.0 [31 32 33] 2.0 [31 32 33]
33.0 [32 33 34] 2.0 [32 33 34]
34.0 [33 34 35] 2.0 [33 34 35]
35.

694.0 [693 694 695] 2.0 [693 694 695]
695.0 [694 695 696] 2.0 [694 695 696]
696.0 [695 696 697] 2.0 [695 696 697]
697.0 [696 697 698] 2.0 [696 697 698]
698.0 [697 698 699] 2.0 [697 698 699]
699.0 [698 699 700] 2.0 [698 699 700]
700.0 [699 700 701] 2.0 [699 700 701]
701.0 [700 701 702] 2.0 [700 701 702]
702.0 [701 702 703] 2.0 [701 702 703]
703.0 [702 703 704] 2.0 [702 703 704]
704.0 [703 704 705] 2.0 [703 704 705]
705.0 [704 705 706] 2.0 [704 705 706]
706.0 [705 706 707] 2.0 [705 706 707]
707.0 [706 707 708] 2.0 [706 707 708]
708.0 [707 708 709] 2.0 [707 708 709]
709.0 [708 709 710] 2.0 [708 709 710]
710.0 [709 710 711] 2.0 [709 710 711]
711.0 [710 711 712] 2.0 [710 711 712]
712.0 [711 712 713] 2.0 [711 712 713]
713.0 [712 713 714] 2.0 [712 713 714]
714.0 [713 714 715] 2.0 [713 714 715]
715.0 [714 715 716] 2.0 [714 715 716]
716.0 [715 716 717] 2.0 [715 716 717]
717.0 [716 717 718] 2.0 [716 717 718]
718.0 [717 718 719] 2.0 [717 718 719]
719.0 [718 719 720] 2.0 [718 719 720]
720.0 [719 7

In [6]:
z, w = dem_z(hdm, 1024)
px.line(y=[z[0].squeeze(), z[1].squeeze(), *w[0].T])

In [11]:
px.line(y=[*gen.x[:, 0, :, 0].T] + [*y.T])

In [12]:
hdm[0]['x']  = np.array([[12,13,16]])
hdm[0]['pC'] = np.diag(np.ones(pE.shape)) * np.exp(-128)
# hdm[0]['V'] *= np.exp()

deminv = DEMInversion(hdm, states_embedding_order=6)
dec    = deminv.run(y)

E-step (F = -inf):   0%|          | 0/8 [00:00<?, ?it/s]

timestep:   0%|          | 0/1024 [00:00<?, ?it/s]

In [14]:
dec

{'F': array([-996788.32469489, -996788.32469489,              nan,
                     nan,              nan,              nan,
                     nan,              nan]),
 'A': array([-961299.18905022, -961299.18905022,              nan,
                     nan,              nan,              nan,
                     nan,              nan]),
 'qH': {'h': array([], shape=(0, 1), dtype=float64),
  'C': array([], shape=(0, 0), dtype=float64)},
 'qP': {'P': array([[18.  ],
         [18.  ],
         [46.92],
         [ 2.  ],
         [ 1.  ],
         [ 2.  ],
         [ 4.  ],
         [ 1.  ],
         [ 1.  ],
         [ 1.  ]]),
  'C': array([[ 2.57220937e-056,  6.06099473e-100,  0.00000000e+000,
           0.00000000e+000,  0.00000000e+000,  0.00000000e+000,
           0.00000000e+000,  0.00000000e+000,  0.00000000e+000,
           0.00000000e+000],
         [ 6.06099473e-100,  2.57220937e-056,  0.00000000e+000,
           0.00000000e+000,  0.00000000e+000,  0.00000000e+000,
  

In [13]:
px.line(y=[*(dec.qU.x[:, 0] - gen.x[:, 0, :, 0]).T])

In [9]:
fig = pk.SysWrapper(dec.qU.x[128:, 0, :]).plot(show=False)
pk.SysWrapper(gen.x[128:, 0, :, 0]).plot(fig=fig, show=False)
fig.update_layout(template='simple_white')

In [9]:
px.line(y=[*dec.qU.x[:, 0, :].T] + [*gen.x[:, 0, :, 0].T]).show()
px.line(y=[*dec.qU.y[:, 0, :].T] + [*y[:, :].T]).show()

In [8]:
hdm[0].x[0]

array([12, 13, 16])

In [9]:
from plotly.subplots import make_subplots
fig   = make_subplots(cols=2, rows=2)#, column_titles=['$(x, y)$', '$(x,z)$'])
color = px.colors.qualitative.Pastel[2]

for i in range(2): 
    fig.add_scatter(x=dec.qU.x[:, 0, 0], y=dec.qU.x[:, 0, 1], line_color=color, 
                    line_width=1, opacity=1, legendgroup='estimated', name='Estimated', showlegend=i==0, row=i+1, col=1)
    fig.add_scatter(x=dec.qU.x[:, 0, 0], y=dec.qU.x[:, 0, 2], line_color=color, 
                    line_width=1, opacity=1, legendgroup='estimated', showlegend=False, row=i+1, col=2)

    fig.add_scatter(x=gen.x[:, 0, 0, 0], y=gen.x[:, 0, 1, 0], line_color='black', line_dash='dash', 
                    line_width=1, legendgroup='realized', name='Realized', showlegend=i==0, opacity=0.7, row=i+1, col=1)
    fig.add_scatter(x=gen.x[:, 0, 0, 0], y=gen.x[:, 0, 2, 0], line_color='black', line_dash='dash', 
                    line_width=1, legendgroup='realized', showlegend=False, row=i+1, col=2)
    
    fig.add_scatter(mode='markers', x=[.9], y=[.8], marker_color='black', showlegend=False, marker_size=10, row=i+1, col=1)
    fig.add_scatter(mode='markers', x=[.9], y=[30.], marker_color='black', showlegend=False, marker_size=10, row=i+1, col=2)

    fig.add_scatter(mode='markers', x=[hdm[0].x[0, 0]], y=[hdm[0].x[0, 1]], showlegend=False, marker_color=color, marker_size=10, row=i+1, col=1)
    fig.add_scatter(mode='markers', x=[hdm[0].x[0, 0]], y=[hdm[0].x[0, 2]], showlegend=False, marker_color=color, marker_size=10, row=i+1, col=2)

fig.update_xaxes(title_text='$x$', title_standoff=0, mirror=True)
fig.update_yaxes(title_standoff=0, mirror=True)

fig.update_xaxes(range=(-16, 16), row=1, col=1)
fig.update_yaxes(range=(-20, 20), title_text='$y$', row=1, col=1)

fig.update_xaxes(range=(-16, 16), row=1, col=2)
fig.update_yaxes(range=(5, 40), title_text='$z$', row=1, col=2)

fig.update_xaxes(range=(-5, 5), row=2, col=1)
fig.update_yaxes(range=(-5, 5), title_text='$y$', row=2, col=1)

fig.update_xaxes(range=(-5, 5), row=2, col=2)
fig.update_yaxes(range=(12, 27), title_text='$z$', row=2, col=2)
fig.update_layout(template='simple_white', width=800, height=800, 
                 legend=dict(orientation="h",
                    yanchor="bottom",
                    y=1.01,
                    xanchor="left",
                    x=0.01)
)
fig.show()
fig.write_image('/home/yop/Images/manuscript/DEM/lorenz_inversion_2d_zoom.png')
fig.write_image('/home/yop/Images/manuscript/DEM/lorenz_inversion_2d_zoom.pdf')


In [10]:
trajs = []
for j, initial_states in enumerate(([12,13,16], [8,0,30], [0, 10, 24], [5, 5,8], [17,2,35],  [5, 15,16])):
    hdm[0]['x'] = torch.DoubleTensor(initial_states)
    deminv = DEMInversion(hdm, states_embedding_order=4)
    dec    = deminv.run(y, nD=1, nE=1, nM=1)
    trajs.append(dec)

timestep:   0%|          | 0/1024 [00:00<?, ?it/s]

timestep:   0%|          | 0/1024 [00:00<?, ?it/s]

timestep:   0%|          | 0/1024 [00:00<?, ?it/s]

timestep:   0%|          | 0/1024 [00:00<?, ?it/s]

timestep:   0%|          | 0/1024 [00:00<?, ?it/s]

timestep:   0%|          | 0/1024 [00:00<?, ?it/s]

In [11]:
from plotly.subplots import make_subplots
fig   = make_subplots(cols=2, rows=2)#, column_titles=['$(x, y)$', '$(x,z)$'])
for j, initial_states in enumerate(([12,13,16], [8,0,30], [0, 10, 24], [5, 5,8], [17,2,35],  [5, 15,16])):
    if j == 4: continue 
    dec = trajs[j]

    color = px.colors.qualitative.Pastel[j+1]

    for i in range(2): 
        fig.add_scatter(x=dec.qU.x[:, 0, 0], y=dec.qU.x[:, 0, 1], line_color=color, 
                        line_width=1, opacity=.8, legendgroup=f'{initial_states}', name=f'{initial_states}', showlegend=i==0, row=i+1, col=1)
        fig.add_scatter(x=dec.qU.x[:, 0, 0], y=dec.qU.x[:, 0, 2], line_color=color, 
                        line_width=1, opacity=.8, legendgroup=f'{initial_states}', showlegend=False, row=i+1, col=2)

for i in range(2): 
    fig.add_scatter(x=gen.x[:, 0, 0, 0], y=gen.x[:, 0, 1, 0], line_color='black', line_dash='dash', 
                    line_width=1, legendgroup='realized', name='Realized', showlegend=i==0, opacity=0.7, row=i+1, col=1)
    fig.add_scatter(x=gen.x[:, 0, 0, 0], y=gen.x[:, 0, 2, 0], line_color='black', line_dash='dash', 
                    line_width=1, legendgroup='realized', showlegend=False, row=i+1, col=2)

    fig.add_scatter(mode='markers', x=[.9], y=[.8], marker_color='black', showlegend=False, marker_size=10, row=i+1, col=1)
    fig.add_scatter(mode='markers', x=[.9], y=[30.], marker_color='black', showlegend=False, marker_size=10, row=i+1, col=2)

for j, initial_states in enumerate(([12,13,16], [8,0,30], [0, 10, 24], [5, 5,8], [17,2,35],  [5, 15,16])):
    if j == 4: continue 
    
    dec = trajs[j]
    color = px.colors.qualitative.Pastel[j+1]
    
    for i in range(2): 
    
        fig.add_scatter(mode='markers', x=[dec.qU.x[0,0,0].item()], y=[dec.qU.x[0,0,1].item()], legendgroup=f'{initial_states}',
                        showlegend=False, marker_color=color, marker_size=10, row=i+1, col=1)
        fig.add_scatter(mode='markers', x=[dec.qU.x[0,0,0].item()], y=[dec.qU.x[0,0,2].item()], legendgroup=f'{initial_states}',
                        showlegend=False, marker_color=color, marker_size=10, row=i+1, col=2)
    
fig.update_xaxes(title_text='$x$', title_standoff=0, mirror=True)
fig.update_yaxes(title_standoff=0, mirror=True)

fig.update_xaxes(range=(-16, 16), row=1, col=1)
fig.update_yaxes(range=(-20, 20), title_text='$y$', row=1, col=1)

fig.update_xaxes(range=(-16, 16), row=1, col=2)
fig.update_yaxes(range=(5, 40), title_text='$z$', row=1, col=2)

fig.update_xaxes(range=(-5, 5), row=2, col=1)
fig.update_yaxes(range=(-5, 5), title_text='$y$', row=2, col=1)

fig.update_xaxes(range=(-5, 5), row=2, col=2)
fig.update_yaxes(range=(12, 27), title_text='$z$', row=2, col=2)
fig.update_layout(template='simple_white', width=800, height=800, 
                 legend=dict(
                      orientation='h',
                    yanchor="bottom",
                    y=1.01,
                    xanchor="left",
                    x=0.01)
)
fig.show()
fig.write_image('/home/yop/Images/manuscript/DEM/lorenz_inversion_2d_zoom_multiple.png')
fig.write_image('/home/yop/Images/manuscript/DEM/lorenz_inversion_2d_zoom_multiple.pdf')


In [ ]:
import sympy
sympy.SparseMatrix((3, 3)).jacobian

In [ ]:
fig = go.Figure()
## TAKE VALUES FROM SPM TOOLBOXES
for i, initial_states in enumerate(([12,13,16], [8,0,30], [0, 10, 24], [5, 5,8], [17,2,35],  [5, 15,16])):

    fig.add_scatter(x=dec.qU.x[:, 0, 0], y=dec.qU.x[:, 0, 1], line_color=px.colors.qualitative.Pastel[i + 1], opacity=0.7)
    fig.add_scatter(mode='markers', x=[hdm[0].x[0].item()], y=[hdm[0].x[1].item()], marker_color=px.colors.qualitative.Pastel[i + 1], marker_size=10)
    
    
fig.add_scatter(x=gen.x[:, 0, 0, 0], y=gen.x[:, 0, 1, 0], line_color='black', line_dash='dash')
fig.add_scatter(mode='markers', x=[.9], y=[.8], marker_color='black', marker_size=10)
fig.update_xaxes(range=(-20, 20))
fig.update_yaxes(range=(-20, 20))
fig.update_layout(template='simple_white', width=600, height=600)

In [ ]:
fig = go.Figure()
# y = traj['y'][None]

for i, initial_states in enumerate(([12,13,16], [8,0,30], [0, 10, 24], [5, 5,8], [17,2,35],  [5, 15,16])):
    y = state_space.sample(512)['y'][None]
    
    model_parameters['initial_state_mean'] = torch.tensor([float(v) for v in initial_states])
    fit_model = GaussianStateSpaceModel(**model_parameters)
    traj_filt = fit_model.filter(y, backward_pass=True)
    
    pk.SysWrapper(ts=traj_filt['x_prev'].mean[0, :, :2]).plot(fig=fig, show=False, 
                                                              line_color=px.colors.qualitative.Pastel[i+1], name=f'{initial_states}', legendgroup=f'{i+1}', opacity=0.7);
    fig.add_scatter(x=[initial_states[0]],y=[initial_states[1]], mode='markers', 
                    marker_color=px.colors.qualitative.Pastel[i+1], marker_size=10, legendgroup=f'{i+1}', showlegend=False)
    
# pk.SysWrapper(ts=traj_filt['x_prev'].mean[0, :, :2]).plot(fig=fig, show=False);

pk.SysWrapper(ts=traj['x'].mean[:, :2]).plot(fig=fig, show=False, line_color='black', line_dash='dash', name=f'Reference', opacity=0.8);
fig.add_scatter(x=[0.9],y=[0.8], mode='markers', marker_color='black', marker_size=10, showlegend=False)

fig.update_xaxes(range=(-20,24))
fig.update_yaxes(range=(-20,24))
fig.update_layout(height=600, width=600, template='simple_white', title={'text':'attractor reconstruction (EKF)',
         'x':0.5,
         'xanchor': 'center'})
fig.show()

In [ ]:
for i in range(10): 
    trajectory = state_space.filter(measurements[None, ...], backward_pass=True)
    A.fit(trajectory['x_backward'].mean[:, :-1], trajectory['x_backward'].mean[:, 1:])
    H.fit(trajectory['x_backward'].mean, measurements[None])
    state_space.fit_params(measurements[None], trajectory)    
    plot_traj(trajectory['x_backward']).show()
    plot_traj(trajectory['y_prior']).show()
    
    ll.append(state_space.complete_data_likelihood(measurements[None], trajectory))
    print(ll[-1])